# Regression Week 2: Multiple Regression (Interpretation)

The goal of this first notebook is to explore multiple regression and feature engineering with existing graphlab functions.

In this notebook you will use data on house sales in King County to predict prices using multiple regression. You will:
* Use SFrames to do some feature engineering
* Use built-in graphlab functions to compute the regression weights (coefficients/parameters)
* Given the regression weights, predictors and outcome write a function to compute the Residual Sum of Squares
* Look at coefficients and interpret their meanings
* Evaluate multiple models via RSS

# Fire up graphlab create

In [5]:
import graphlab
graphlab.canvas.set_target('ipynb')

# Load in house sales data

Dataset is from house sales in King County, the region where the city of Seattle, WA is located.

In [3]:
sales = graphlab.SFrame('data/kc_house_data.gl/')

In [7]:
print sales.shape
sales.show()

(21613, 21)


# Split data into training and testing.
We use seed=0 so that everyone running this notebook gets the same results.  In practice, you may set a random seed (or let GraphLab Create pick a random seed for you).  

In [4]:
train_data,test_data = sales.random_split(.8,seed=0)

In [8]:
print train_data.shape
train_data.show()

(17384, 21)


In [9]:
print test_data.shape
test_data.show()

(4229, 21)


# Learning a multiple regression model

Recall we can use the following code to learn a multiple regression model predicting 'price' based on the following features:
example_features = ['sqft_living', 'bedrooms', 'bathrooms'] on training data with the following code:

(Aside: We set validation_set = None to ensure that the results are always the same)

In [10]:
example_features = ['sqft_living', 'bedrooms', 'bathrooms']
example_model = graphlab.linear_regression.create(train_data, \
                            target = 'price', features = example_features, 
                            validation_set = None)

PROGRESS: Linear regression:
PROGRESS: --------------------------------------------------------
PROGRESS: Number of examples          : 17384
PROGRESS: Number of features          : 3
PROGRESS: Number of unpacked features : 3
PROGRESS: Number of coefficients    : 4
PROGRESS: Starting Newton Method
PROGRESS: --------------------------------------------------------
PROGRESS: +-----------+----------+--------------+--------------------+---------------+
PROGRESS: | Iteration | Passes   | Elapsed Time | Training-max_error | Training-rmse |
PROGRESS: +-----------+----------+--------------+--------------------+---------------+
PROGRESS: | 1         | 2        | 1.146982     | 4146407.600631     | 258679.804477 |
PROGRESS: +-----------+----------+--------------+--------------------+---------------+
PROGRESS: SUCCESS: Optimal solution found.
PROGRESS:


Now that we have fitted the model we can extract the regression weights (coefficients) as an SFrame as follows:

In [11]:
example_weight_summary = example_model.get("coefficients")
print example_weight_summary

+-------------+-------+----------------+
|     name    | index |     value      |
+-------------+-------+----------------+
| (intercept) |  None | 87910.0724924  |
| sqft_living |  None | 315.403440552  |
|   bedrooms  |  None | -65080.2155528 |
|  bathrooms  |  None | 6944.02019265  |
+-------------+-------+----------------+
[4 rows x 3 columns]



# Making Predictions

In the gradient descent notebook we use numpy to do our regression. In this book we will use existing graphlab create functions to analyze multiple regressions. 

Recall that once a model is built we can use the .predict() function to find the predicted values for data we pass. For example using the example model above:

In [12]:
example_predictions = example_model.predict(train_data)
print example_predictions[0] # should be 271789.505878

271789.505878


# Compute RSS

Now that we can make predictions given the model, let's write a function to compute the RSS of the model. Complete the function below to calculate RSS given the model, data, and the outcome.

In [19]:
def get_residual_sum_of_squares(model, data, outcome):
    # First get the predictions
    predictions = model.predict(data)
    
    # Then compute the residuals/errors
    residuals = outcome - predictions

    # Then square and add them up
    RSS = (residuals * residuals).sum()

    return(RSS)    

Test your function by computing the RSS on TEST data for the example model:

In [20]:
rss_example_test = get_residual_sum_of_squares(example_model, \
                                            test_data, test_data['price'])
print rss_example_test # should be 2.7376153833e+14

2.7376153833e+14


# Create some new features

Although we often think of multiple regression as including multiple different features (e.g. # of bedrooms, squarefeet, and # of bathrooms) but we can also consider transformations of existing features e.g. the log of the squarefeet or even "interaction" features such as the product of bedrooms and bathrooms.

You will use the logarithm function to create a new feature. so first you should import it from the math library.

In [21]:
from math import log

Next create the following 4 new features as column in both TEST and TRAIN data:
* bedrooms_squared = bedrooms\*bedrooms
* bed_bath_rooms = bedrooms\*bathrooms
* log_sqft_living = log(sqft_living)
* lat_plus_long = lat + long 
As an example here's the first one:

In [22]:
train_data['bedrooms_squared'] = train_data['bedrooms'].apply(lambda x: x**2)
test_data['bedrooms_squared'] = test_data['bedrooms'].apply(lambda x: x**2)
train_data[['bedrooms', 'bedrooms_squared']].show()

In [23]:
# create the remaining 3 features in both TEST and TRAIN data
train_data['bed_bath_rooms'] = train_data['bedrooms'] * \
                               train_data['bathrooms']
test_data['bed_bath_rooms'] = test_data['bedrooms'] * \
                               test_data['bathrooms']
train_data[['bedrooms','bathrooms', 'bed_bath_rooms']].show()


In [36]:
print log(2.0); print log(2); print graphlab.SArray([3.0, 3]).apply(log)
print type(train_data['sqft_living'])
print train_data['sqft_living'][1:5]
print train_data['sqft_living'][1:5].apply(log)

0.69314718056
0.69314718056
[1.0986122886681098, 1.0986122886681098]
<class 'graphlab.data_structures.sarray.SArray'>
[2570.0, 770.0, 1960.0, 1680.0]
[7.851661177889265, 6.646390514847729, 7.580699752224563, 7.426549072397305]


In [35]:
train_data['log_sqft_living'] = train_data['sqft_living'].apply(log)
test_data['log_sqft_living'] = test_data['sqft_living'].apply(log)
train_data[['sqft_living','log_sqft_living']].show()

In [37]:
train_data['lat_plus_long'] = train_data['lat'] + train_data['long']  
test_data['lat_plus_long'] = test_data['lat'] + test_data['long']  
train_data[['lat','long', 'lat_plus_long']].show()

* Squaring bedrooms will increase the separation between not many bedrooms (e.g. 1) and lots of bedrooms (e.g. 4) since 1^2 = 1 but 4^2 = 16. Consequently this feature will mostly affect houses with many bedrooms.
* bedrooms times bathrooms gives what's called an "interaction" feature. It is large when *both* of them are large.
* Taking the log of squarefeet has the effect of bringing large values closer together and spreading out small values.
* Adding latitude to longitude is totally non-sensical but we will do it anyway (you'll see why)

**Quiz Question: What is the mean (arithmetic average) value of your 4 new features on TEST data? (round to 2 digits)**

In [41]:
print [round(test_data[feat].mean(), 2) for feat in \
           ['bedrooms_squared','bed_bath_rooms','log_sqft_living',\
            'lat_plus_long']]

[12.45, 7.5, 7.55, -74.65]


# Learning Multiple Models

Now we will learn the weights for three (nested) models for predicting house prices. The first model will have the fewest features the second model will add one more feature and the third will add a few more:
* Model 1: squarefeet, # bedrooms, # bathrooms, latitude & longitude
* Model 2: add bedrooms\*bathrooms
* Model 3: Add log squarefeet, bedrooms squared, and the (nonsensical) latitude + longitude

In [42]:
model_1_features = ['sqft_living', 'bedrooms', 'bathrooms', 'lat', 'long']
model_2_features = model_1_features + ['bed_bath_rooms']
model_3_features = model_2_features + \
                ['bedrooms_squared', 'log_sqft_living', 'lat_plus_long']

Now that you have the features, learn the weights for the three different models for predicting target = 'price' using graphlab.linear_regression.create() and look at the value of the weights/coefficients:

In [45]:
# Learn the three models: (don't forget to set validation_set = None)
model_1 = graphlab.linear_regression.create(train_data, \
                            target = 'price', features = model_1_features, 
                            validation_set = None)
model_2 = graphlab.linear_regression.create(train_data, \
                            target = 'price', features = model_2_features, 
                            validation_set = None)
model_3 = graphlab.linear_regression.create(train_data, \
                            target = 'price', features = model_3_features, 
                            validation_set = None)

PROGRESS: Linear regression:
PROGRESS: --------------------------------------------------------
PROGRESS: Number of examples          : 17384
PROGRESS: Number of features          : 5
PROGRESS: Number of unpacked features : 5
PROGRESS: Number of coefficients    : 6
PROGRESS: Starting Newton Method
PROGRESS: --------------------------------------------------------
PROGRESS: +-----------+----------+--------------+--------------------+---------------+
PROGRESS: | Iteration | Passes   | Elapsed Time | Training-max_error | Training-rmse |
PROGRESS: +-----------+----------+--------------+--------------------+---------------+
PROGRESS: | 1         | 2        | 0.252785     | 4074878.213082     | 236378.596455 |
PROGRESS: +-----------+----------+--------------+--------------------+---------------+
PROGRESS: SUCCESS: Optimal solution found.
PROGRESS:
PROGRESS: Linear regression:
PROGRESS: --------------------------------------------------------
PROGRESS: Number of examples          : 17384
PROG

In [46]:
# Examine/extract each model's coefficients:
model_1_weights = model_1.get("coefficients")
model_2_weights = model_2.get("coefficients")
model_3_weights = model_3.get("coefficients")

print "model_1 weights:"; print model_1_weights 
print "model_2 weights:"; print model_2_weights 
print "model_3 weights:"; print model_3_weights 

model_1 weights:
+-------------+-------+----------------+
|     name    | index |     value      |
+-------------+-------+----------------+
| (intercept) |  None | -56140675.7464 |
| sqft_living |  None | 310.263325779  |
|   bedrooms  |  None | -59577.1160686 |
|  bathrooms  |  None | 13811.8405423  |
|     lat     |  None | 629865.789454  |
|     long    |  None | -214790.285215 |
+-------------+-------+----------------+
[6 rows x 3 columns]

model_2 weights:
+----------------+-------+----------------+
|      name      | index |     value      |
+----------------+-------+----------------+
|  (intercept)   |  None | -54410676.117  |
|  sqft_living   |  None | 304.449298058  |
|    bedrooms    |  None | -116366.04323  |
|   bathrooms    |  None | -77972.3305122 |
|      lat       |  None | 625433.834923  |
|      long      |  None | -203958.602986 |
| bed_bath_rooms |  None | 26961.6249089  |
+----------------+-------+----------------+
[7 rows x 3 columns]

model_3 weights:
+----------

**Quiz Question: What is the sign (positive or negative) for the coefficient/weight for 'bathrooms' in model 1?**

**Quiz Question: What is the sign (positive or negative) for the coefficient/weight for 'bathrooms' in model 2?**

Think about what this means.

# Comparing multiple models

Now that you've learned three models and extracted the model weights we want to evaluate which model is best.

First use your functions from earlier to compute the RSS on TRAINING Data for each of the three models.

In [50]:
# Compute the RSS on TRAINING data for each of the three models and
#   record the values:
rss_models_train = {
    'model_1': get_residual_sum_of_squares(model_1, \
                                        train_data, train_data['price']),
    'model_2': get_residual_sum_of_squares(model_2, \
                                        train_data, train_data['price']),
    'model_3': get_residual_sum_of_squares(model_3, \
                                        train_data, train_data['price'])
}
print "rss_models_train: %s" % (rss_models_train)

rss_models_train: {'model_1': 971328233542723.4, 'model_3': 905276314555216.0, 'model_2': 961592067855009.2}


**Quiz Question: Which model (1, 2 or 3) has lowest RSS on TRAINING Data?** Is this what you expected?

Now compute the RSS on on TEST data for each of the three models.

In [51]:
# Compute the RSS on TESTING data for each of the three models and record the values:
rss_models_test = {
    'model_1': get_residual_sum_of_squares(model_1, \
                                        test_data, test_data['price']),
    'model_2': get_residual_sum_of_squares(model_2, \
                                        test_data, test_data['price']),
    'model_3': get_residual_sum_of_squares(model_3, \
                                        test_data, test_data['price'])
}
print "rss_models_test: %s" % (rss_models_test)

rss_models_test: {'model_1': 226568089092489.3, 'model_3': 251829318949513.72, 'model_2': 224368799993370.12}


**Quiz Question: Which model (1, 2 or 3) has lowest RSS on TESTING Data?** Is this what you expected?Think about the features that were added to each model from the previous.